# Datacenter Score Analysis

This notebook ingests recent market and weather data to compute a composite datacenter siting score across U.S. grid regions.

## Environment Setup
Ensure required dependencies are available for the workflow.

## Imports and Global Configuration


In [1]:
import json
import os
from datetime import datetime, timedelta
from functools import lru_cache
from pathlib import Path

import numpy as np
import pandas as pd
import requests
import plotly.express as px
import matplotlib.pyplot as plt
from prophet import Prophet

plt.style.use('seaborn-v0_8')
px.defaults.template = 'plotly_white'

CACHE_DIR = Path('cache')
CACHE_DIR.mkdir(exist_ok=True)
EIA_BASE_URL = 'https://api.eia.gov/v2/electricity/rto/region-data/data/'
EIA_API_KEY = os.getenv('EIA_API_KEY')
HISTORICAL_DAYS = 90
PROPHET_LOOKBACK_DAYS = 60
FORECAST_HOURS = 24 * 7


## EIA Hourly Demand Fetching


In [2]:
def _cache_path_for_region(region: str) -> Path:
    return CACHE_DIR / f'eia_{region.lower()}_hourly.csv'


@lru_cache(maxsize=None)
def fetch_eia_hourly(region: str) -> pd.DataFrame:
    """Fetch the most recent 90 days of hourly demand for the requested EIA region.

    Parameters
    ----------
    region : str
        The EIA RTO/region code (e.g., 'CAL', 'TEX').

    Returns
    -------
    pd.DataFrame
        DataFrame with columns [datetime, demand_MW, region].
    """
    cache_path = _cache_path_for_region(region)
    end = datetime.utcnow()
    start = end - timedelta(days=HISTORICAL_DAYS)
    params = {
        'api_key': EIA_API_KEY,
        'data[0]': 'value',
        'facets[respondent][]': region,
        'frequency': 'hourly',
        'start': start.strftime('%Y-%m-%dT%H'),
        'end': end.strftime('%Y-%m-%dT%H'),
        'sort[0][column]': 'period',
        'sort[0][direction]': 'desc',
        'offset': 0,
        'length': 5000,
    }
    try:
        response = requests.get(EIA_BASE_URL, params=params, timeout=30)
        response.raise_for_status()
        payload = response.json()
        data = payload.get('response', {}).get('data', [])
        if not data:
            raise ValueError('Empty dataset returned from EIA API.')
        records = []
        for item in data:
            period = item.get('period')
            value = item.get('value')
            if period is None or value is None:
                continue
            records.append({
                'datetime': pd.to_datetime(period),
                'demand_MW': float(value),
                'region': region,
            })
        df = pd.DataFrame(records)
        if df.empty:
            raise ValueError('No valid records parsed from EIA response.')
        df = df.drop_duplicates(subset='datetime').sort_values('datetime')
        df = df[df['datetime'] >= start]
        df.to_csv(cache_path, index=False)
        return df
    except Exception as exc:
        print(f'EIA API fetch failed for {region}: {exc}')
        if cache_path.exists():
            print(f'Loading cached data for {region} from {cache_path}.')
            df = pd.read_csv(cache_path, parse_dates=['datetime'])
            return df
        raise


## Forecasting and Grid Metrics


In [3]:
def _prepare_hourly_series(df_region: pd.DataFrame) -> pd.DataFrame:
    if df_region.empty:
        raise ValueError('Region dataframe is empty.')
    df = df_region.copy()
    df = df.drop_duplicates(subset='datetime').sort_values('datetime')
    df = df.set_index('datetime')
    full_range = pd.date_range(df.index.min(), df.index.max(), freq='H')
    df = df.reindex(full_range)
    df['demand_MW'] = df['demand_MW'].interpolate(method='time')
    df['region'] = df_region['region'].iloc[0]
    return df


def forecast_peak_demand(df_region: pd.DataFrame) -> float:
    prepped = _prepare_hourly_series(df_region)
    recent_start = prepped.index.max() - timedelta(days=PROPHET_LOOKBACK_DAYS)
    df_recent = prepped[prepped.index >= recent_start]
    prophet_df = df_recent.reset_index().rename(columns={'index': 'ds', 'demand_MW': 'y'})
    model = Prophet(
        growth='flat',
        daily_seasonality=True,
        weekly_seasonality=True,
        yearly_seasonality=False
    )
    model.add_country_holidays(country_name='US')
    model.fit(prophet_df)
    future = model.make_future_dataframe(periods=FORECAST_HOURS, freq='H', include_history=False)
    forecast = model.predict(future)
    peak_forecast = float(forecast['yhat'].max())
    return peak_forecast


def compute_volatility(df_region: pd.DataFrame) -> float:
    prepped = _prepare_hourly_series(df_region)
    rolling_std = prepped['demand_MW'].rolling(window=24, min_periods=1).std()
    return float(rolling_std.iloc[-1])


def compute_renewable_proxy(df_region: pd.DataFrame) -> float:
    prepped = _prepare_hourly_series(df_region)
    mean_load = prepped['demand_MW'].mean()
    return float(1.0 / (1.0 + mean_load))


def compute_carbon_proxy(renewable_proxy: float) -> float:
    return float(1.0 - renewable_proxy)


## Weather Data via Open-Meteo


In [4]:
@lru_cache(maxsize=None)
def fetch_temperature(lat: float, lon: float) -> float:
    url = 'https://api.open-meteo.com/v1/forecast'
    params = {
        'latitude': lat,
        'longitude': lon,
        'daily': 'temperature_2m_mean',
        'past_days': 60,
        'timezone': 'UTC',
    }
    try:
        response = requests.get(url, params=params, timeout=30)
        response.raise_for_status()
        data = response.json()
        temps = data.get('daily', {}).get('temperature_2m_mean', [])
        if not temps:
            raise ValueError('Temperature series is empty.')
        return float(np.mean(temps))
    except Exception as exc:
        print(f'Open-Meteo fetch failed for ({lat}, {lon}): {exc}')
        return float('nan')


region_coords = {
    'CAL': (36.5, -119.5),
    'CAR': (35.5, -80.0),
    'CENT': (38.5, -94.5),
    'FLA': (28.0, -82.0),
    'MIDA': (39.0, -77.0),
    'MIDW': (42.0, -89.0),
    'NE': (42.5, -72.5),
    'NY': (42.9, -75.3),
    'NW': (45.5, -120.5),
    'SE': (33.0, -84.0),
    'SW': (36.0, -111.5),
    'TEN': (36.0, -86.0),
    'TEX': (31.0, -99.0),
}


## Compute Datacenter Scores


In [5]:
records = []
for region, (lat, lon) in region_coords.items():
    try:
        df_region = fetch_eia_hourly(region)
    except Exception as exc:
        print(f'Skipping region {region} due to data issues: {exc}')
        continue
    df_region = df_region.sort_values('datetime')
    latest_demand = float(df_region['demand_MW'].iloc[-1]) if not df_region.empty else float('nan')
    volatility = compute_volatility(df_region)
    peak = forecast_peak_demand(df_region)
    renewable_proxy = compute_renewable_proxy(df_region)
    carbon_proxy = compute_carbon_proxy(renewable_proxy)
    avg_temp = fetch_temperature(lat, lon)
    records.append({
        'region': region,
        'price': latest_demand,
        'peak_forecast': peak,
        'volatility': volatility,
        'renewable_proxy': renewable_proxy,
        'carbon_proxy': carbon_proxy,
        'avg_temp': avg_temp,
        'lat': lat,
        'lon': lon,
    })

dc_df = pd.DataFrame(records)
if dc_df.empty:
    dc_df = pd.DataFrame(columns=['region', 'price', 'peak_forecast', 'volatility', 'renewable_proxy', 'carbon_proxy', 'avg_temp', 'lat', 'lon'])
else:
    metrics_to_normalize = {
        'price': 'price_norm',
        'peak_forecast': 'peak_norm',
        'volatility': 'volatility_norm',
        'renewable_proxy': 'renewable_norm',
        'carbon_proxy': 'carbon_norm',
        'avg_temp': 'temp_norm',
    }
    for metric, norm_col in metrics_to_normalize.items():
        col = dc_df[metric]
        col_min, col_max = col.min(), col.max()
        if np.isfinite(col_min) and np.isfinite(col_max) and col_max != col_min:
            dc_df[norm_col] = (col - col_min) / (col_max - col_min)
        else:
            dc_df[norm_col] = 0.0
    dc_df['profitability'] = (
        0.40 * (1 - dc_df['price_norm']) +
        0.30 * (1 - dc_df['peak_norm']) +
        0.30 * (1 - dc_df['volatility_norm'])
    )
    dc_df['sustainability'] = (
        0.35 * dc_df['renewable_norm'] +
        0.30 * (1 - dc_df['carbon_norm']) +
        0.20 * (1 - dc_df['temp_norm']) +
        0.15 * dc_df['renewable_norm']
    )
    dc_df['hybrid'] = 0.5 * dc_df['profitability'] + 0.5 * dc_df['sustainability']
    dc_df = dc_df.sort_values('hybrid', ascending=False).reset_index(drop=True)

final_columns = ['region', 'price', 'peak_forecast', 'volatility', 'renewable_proxy', 'carbon_proxy', 'avg_temp', 'profitability', 'sustainability', 'hybrid', 'lat', 'lon']
for col in final_columns:
    if col not in dc_df.columns:
        dc_df[col] = np.nan
dc_df_final = dc_df[final_columns]
dc_df_final.to_csv('datacenter_scores.csv', index=False)
dc_df_final

/var/folders/h3/f3_68x516pj6d7h2119r5st00000gn/T/ipykernel_13246/2527220025.py:20: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  end = datetime.utcnow()
/var/folders/h3/f3_68x516pj6d7h2119r5st00000gn/T/ipykernel_13246/271384653.py:7: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  full_range = pd.date_range(df.index.min(), df.index.max(), freq='H')
/var/folders/h3/f3_68x516pj6d7h2119r5st00000gn/T/ipykernel_13246/271384653.py:7: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  full_range = pd.date_range(df.index.min(), df.index.max(), freq='H')
17:44:45 - cmdstanpy - INFO - Chain [1] start processing
17:44:46 - cmdstanpy - INFO - Chain [1] done processing
/Library/Frameworks/Python.framework/Versions/3.13/lib/python3.13/site-pack

region    price  peak_forecast   volatility  renewable_proxy  carbon_proxy  \
0      NE  14281.0   14815.092594  1349.842357         0.000085      0.999915   
1      SW  13342.0   16138.303647  1074.550664         0.000077      0.999923   
2      NY  17584.0   18571.886568  1231.498780         0.000065      0.999935   
3     TEN  16999.0   20007.030074   913.664381         0.000058      0.999942   
4     CAR  20094.0   27098.281604  1084.047962         0.000044      0.999956   
5      SE  23715.0   29168.618695  1062.322023         0.000041      0.999959   
6     CAL  25823.0   34970.837910  2052.887341         0.000033      0.999967   
7    CENT  32227.0   35350.984142  2132.303876         0.000032      0.999968   
8      NW  38763.0   43670.035348  3034.516579         0.000026      0.999974   
9     FLA  27256.0   37584.148560  3738.783934         0.000034      0.999966   
10    TEX  58173.0   65256.592538  6061.088099         0.000019      0.999981   
11   MIDW  77753.0   86885.621641  4530.276472         0.000013      0.999987   
12   MIDA  87411.0   98089.459107  4213.458793         0.000012      0.999988   

     avg_temp  profitability  sustainability    hybrid   lat    lon  
0   10.041791       0.969508        0.975314  0.972411  42.5  -72.5  
1   13.867164       0.985856        0.838400  0.912128  36.0 -111.5  
2    8.297015       0.945034        0.781354  0.863194  42.9  -75.3  
3   16.362687       0.961547        0.594153  0.777850  36.0  -86.0  
4   16.186567       0.909356        0.439099  0.674227  35.5  -80.0  
5   17.438806       0.883609        0.392233  0.637921  33.0  -84.0  
6   18.038806       0.793590        0.296763  0.545176  36.5 -119.5  
7   16.005970       0.753008        0.310548  0.531778  38.5  -94.5  
8   10.707463       0.635159        0.319979  0.477569  45.5 -120.5  
9   22.432836       0.678180        0.246441  0.462310  28.0  -82.0  
10  21.577612       0.276178        0.089391  0.182785  31.0  -99.0  
11  12.608955       0.181737        0.156401  0.169069  42.0  -89.0  
12  14.308955       0.107683        0.114940  0.111312  39.0  -77.0

## Visualize Scores


In [6]:
if not dc_df_final.empty:
    melted = dc_df_final.melt(id_vars=['region'], value_vars=['profitability', 'sustainability', 'hybrid'], var_name='metric', value_name='score')
    fig = px.bar(melted, x='region', y='score', color='metric', barmode='group', title='Datacenter Score Components by Region')
    fig.show()
else:
    print('No data available for bar chart visualization.')


In [7]:
dc_df_final

region    price  peak_forecast   volatility  renewable_proxy  carbon_proxy  \
0      NE  14281.0   14815.092594  1349.842357         0.000085      0.999915   
1      SW  13342.0   16138.303647  1074.550664         0.000077      0.999923   
2      NY  17584.0   18571.886568  1231.498780         0.000065      0.999935   
3     TEN  16999.0   20007.030074   913.664381         0.000058      0.999942   
4     CAR  20094.0   27098.281604  1084.047962         0.000044      0.999956   
5      SE  23715.0   29168.618695  1062.322023         0.000041      0.999959   
6     CAL  25823.0   34970.837910  2052.887341         0.000033      0.999967   
7    CENT  32227.0   35350.984142  2132.303876         0.000032      0.999968   
8      NW  38763.0   43670.035348  3034.516579         0.000026      0.999974   
9     FLA  27256.0   37584.148560  3738.783934         0.000034      0.999966   
10    TEX  58173.0   65256.592538  6061.088099         0.000019      0.999981   
11   MIDW  77753.0   86885.621641  4530.276472         0.000013      0.999987   
12   MIDA  87411.0   98089.459107  4213.458793         0.000012      0.999988   

     avg_temp  profitability  sustainability    hybrid   lat    lon  
0   10.041791       0.969508        0.975314  0.972411  42.5  -72.5  
1   13.867164       0.985856        0.838400  0.912128  36.0 -111.5  
2    8.297015       0.945034        0.781354  0.863194  42.9  -75.3  
3   16.362687       0.961547        0.594153  0.777850  36.0  -86.0  
4   16.186567       0.909356        0.439099  0.674227  35.5  -80.0  
5   17.438806       0.883609        0.392233  0.637921  33.0  -84.0  
6   18.038806       0.793590        0.296763  0.545176  36.5 -119.5  
7   16.005970       0.753008        0.310548  0.531778  38.5  -94.5  
8   10.707463       0.635159        0.319979  0.477569  45.5 -120.5  
9   22.432836       0.678180        0.246441  0.462310  28.0  -82.0  
10  21.577612       0.276178        0.089391  0.182785  31.0  -99.0  
11  12.608955       0.181737        0.156401  0.169069  42.0  -89.0  
12  14.308955       0.107683        0.114940  0.111312  39.0  -77.0

In [8]:
fig_map = px.scatter_geo(
    dc_df_final,
    lat='lat',
    lon='lon',
    size='hybrid',
    color='hybrid',
    hover_name='region',
    projection='albers usa',
    title='Hybrid Datacenter Score Across U.S. Grid Regions'
)
fig_map.show()

In [9]:
# import h3
# import geopandas as gpd
# from shapely.geometry import Polygon, mapping
# import matplotlib
# import folium
# import mapclassify
# from pathlib import Path
# from zipfile import ZipFile

# try:
#     import geodatasets
# except ImportError as exc:
#     raise ImportError(
#         "Install geodatasets>=2024.8.0 to access the Natural Earth outline:"
#         " pip install geodatasets"
#     ) from exc

# HEX_RES = 4

# land_zip = Path(geodatasets.get_path("naturalearth.land"))
# land_dir = land_zip.with_suffix("")
# if not land_dir.exists():
#     with ZipFile(land_zip) as zf:
#         zf.extractall(land_dir)

# world = gpd.read_file(land_dir / "ne_110m_land.shp")
# name_field = "ADMIN" if "ADMIN" in world.columns else "name"
# us_geom = world.loc[world[name_field] == "United States of America", "geometry"].unary_union
# if us_geom.is_empty:
#     raise ValueError("United States geometry missing in Natural Earth dataset.")
# us_geojson = mapping(us_geom)
# h3_polygon = h3.polygon_to_cells(us_geojson, HEX_RES)

# cells = []
# for h in h3_polygon:
#     boundary = h3.cell_to_boundary(h)
#     poly = Polygon([(lng, lat) for lat, lng in boundary])
#     cells.append({"h3": h, "geometry": poly})

# grid_gdf = gpd.GeoDataFrame(cells, crs="EPSG:4326")

# # Assign datacenter scores to each H3 cell (averaging duplicates)
# dc_hex = dc_df_final.copy()
# dc_hex["h3"] = dc_hex.apply(
#     lambda row: h3.latlng_to_cell(row["lat"], row["lon"], HEX_RES), axis=1
# )
# hex_scores = (
#     dc_hex.groupby("h3")
#     .agg({"hybrid": "mean", "region": "first"})
#     .reset_index()
# )

# gdf_hex = grid_gdf.merge(hex_scores, on="h3", how="left")

# gdf_hex.explore(column="hybrid", cmap="YlOrRd", missing_kwds={"color": "#cccccc"})


In [10]:
# import h3
# import geopandas as gpd
# from shapely.geometry import Polygon, box

# HEX_RES = 4

# # 1. US bounding box as shapely polygon
# us_bounds = box(-125, 24, -66, 50)

# # 2. Convert shapely coords to list of (lat, lng)
# outer = [(lat, lng) for lng, lat in us_bounds.exterior.coords]

# # 3. Build the H3 Polygon (outer ring only)
# poly = h3.LatLngPoly(outer)

# # 4. Generate hex cells within the polygon
# h3_cells = h3.polygon_to_cells(poly, HEX_RES)

# # 5. Convert to shapely polygons
# hex_rows = []
# for h in h3_cells:
#     boundary = h3.cell_to_boundary(h)
#     poly = Polygon([(lng, lat) for lat, lng in boundary])
#     hex_rows.append({"h3": h, "geometry": poly})

# # 6. Convert to GeoDataFrame
# gdf_hex = gpd.GeoDataFrame(hex_rows, crs="EPSG:4326")
# gdf_hex.explore()

In [11]:
# import geopandas as gpd
# from shapely.geometry import Polygon
# import numpy as np

# # 1. Load USA polygon
# usa = gpd.read_file(
#     "https://raw.githubusercontent.com/PublicaMundi/MappingAPI/master/data/geojson/us-states.json"
# )
# usa_border = usa.unary_union
# usa_gdf = gpd.GeoDataFrame(geometry=[usa_border], crs="EPSG:4326")

# # 2. Reproject to Albers Equal Area (CRS suitable for USA)
# usa_proj = usa_gdf.to_crs("EPSG:5070")  # NAD83 / Conus Albers

# # 3. Hex size in METERS (50000 = 50 km hexes)
# HEX_SIZE = 50000

# def make_hex(x, y, size):
#     """Make a perfect hexagon centered at (x,y) in projected coordinates."""
#     angles = np.linspace(0, 2 * np.pi, 7)
#     return Polygon([
#         (x + size * np.cos(a), y + size * np.sin(a)) 
#         for a in angles
#     ])

# # 4. Build bounding box in projected coordinates
# minx, miny, maxx, maxy = usa_proj.total_bounds

# # 5. Generate a hex grid in projected CRS
# hexes = []
# x = minx
# row = 0

# dx = HEX_SIZE * 3/2
# dy = HEX_SIZE * np.sqrt(3) / 2

# y = miny
# while y < maxy + HEX_SIZE:
#     x_offset = (row % 2) * (HEX_SIZE * 0.75)
#     x = minx - HEX_SIZE
#     while x < maxx + HEX_SIZE:
#         hexes.append(make_hex(x + x_offset, y, HEX_SIZE))
#         x += dx
#     y += dy
#     row += 1

# hexgrid_proj = gpd.GeoDataFrame(geometry=hexes, crs="EPSG:5070")

# # 6. Clip hexgrid to US border
# hex_us_proj = gpd.overlay(hexgrid_proj, usa_proj, how="intersection")

# # 7. Reproject back to WGS84 for Folium
# hex_us = hex_us_proj.to_crs("EPSG:4326")

# # 8. Plot
# hex_us.explore()

In [12]:
import geopandas as gpd
from shapely.geometry import Polygon
import numpy as np

# 1. Load USA polygon
usa = gpd.read_file(
    "https://raw.githubusercontent.com/PublicaMundi/MappingAPI/master/data/geojson/us-states.json"
)
usa_border = usa.unary_union
usa_gdf = gpd.GeoDataFrame(geometry=[usa_border], crs="EPSG:4326")

# 2. Reproject to Albers Equal Area (CRS suitable for USA)
usa_proj = usa_gdf.to_crs("EPSG:5070")  # NAD83 / Conus Albers

# 3. Hex radius in meters (distance from center to vertex)
HEX_RADIUS = 50000  # 50 km radius hex

def make_hex(center_x, center_y, radius):
    """Return a perfect pointy-top hexagon polygon with tiny overlap."""
    angles = np.radians(np.arange(30, 390, 60))
    # Add 0.1% overlap to ensure no gaps due to floating point precision
    overlap_factor = 1.001
    return Polygon([
        (center_x + radius * overlap_factor * np.cos(a), 
         center_y + radius * overlap_factor * np.sin(a))
        for a in angles
    ])

# --- Correct tiling spacing ---
hex_width = 2 * HEX_RADIUS                        # flat-to-flat width
hex_height = np.sqrt(3) * HEX_RADIUS              # point-to-point height

dx = np.sqrt(3) * HEX_RADIUS                             # horizontal spacing
dy = 0.865 * hex_height                                    # vertical spacing

# 4. Build bounding box in projected coordinates
minx, miny, maxx, maxy = usa_proj.total_bounds

# 5. Generate hex centers
hexes = []
row = 0
y = miny - hex_height

while y < maxy + hex_height:
    # offset every other row
    x_offset = (row % 2) * (dx / 2)  # = 0.75 * HEX_RADIUS
    x = minx - hex_width
    while x < maxx + hex_width:
        hexes.append(make_hex(x + x_offset, y, HEX_RADIUS))
        x += dx
    y += dy
    row += 1

hexgrid_proj = gpd.GeoDataFrame(geometry=hexes, crs="EPSG:5070")

# 6. Clip hexgrid to US border
hex_us_proj = gpd.overlay(hexgrid_proj, usa_proj, how="intersection")

# 7. Reproject back to WGS84 for Folium / display
hex_us = hex_us_proj.to_crs("EPSG:4326")

# 8. Visualize (geopandas)
hex_us.explore()

/var/folders/h3/f3_68x516pj6d7h2119r5st00000gn/T/ipykernel_13246/2202859732.py:9: DeprecationWarning:

The 'unary_union' attribute is deprecated, use the 'union_all()' method instead.



In [13]:
hex_us_proj

geometry
0     POLYGON ((3141451.345 -27286.571, 3172409.567 ...
1     POLYGON ((3228053.885 -27286.571, 3235079.45 -...
2     POLYGON ((3141494.646 -27450.374, 3121271.989 ...
3     POLYGON ((3228097.187 22599.626, 3228097.187 -...
4     POLYGON ((3228010.584 -27450.374, 3228010.584 ...
...                                                 ...
1718  POLYGON ((-3050630.292 6090242.815, -3066616.3...
1719  POLYGON ((-5475458.121 6192471.238, -5498363.9...
1720  POLYGON ((-5475544.724 6217175.829, -5473456.8...
1721  POLYGON ((-3396997.152 6190179.013, -3439312.3...
1722  POLYGON ((-3397083.755 6190179.013, -3397083.7...

[1723 rows x 1 columns]

In [14]:
# ALL SYNTHETIC DATA, THIS IS JUST A PREVIEW OF WHAT THE MAP COULD POSSIBLY LOOK LIKE
np.random.seed(0)

hex_us_proj["price_raw"]     = np.random.normal(40, 10, len(hex_us_proj))
hex_us_proj["load_raw"]      = np.random.normal(200, 80, len(hex_us_proj))
hex_us_proj["temp_raw"]      = np.random.normal(60, 10, len(hex_us_proj))
hex_us_proj["renew_raw"]     = np.random.uniform(0, 1, len(hex_us_proj))
hex_us_proj["stability_raw"] = np.random.uniform(0.7, 1.0, len(hex_us_proj))
hex_us_proj["co2_raw"]       = np.random.uniform(200, 800, len(hex_us_proj))

for col in ["price_raw","load_raw","temp_raw","renew_raw","stability_raw","co2_raw"]:
    hex_us_proj["n_"+col] = (
        hex_us_proj[col] - hex_us_proj[col].min()
    ) / (hex_us_proj[col].max() - hex_us_proj[col].min())

hex_us_proj["profit"] = (
    0.40*(1 - hex_us_proj["n_price_raw"]) +
    0.35*(hex_us_proj["n_load_raw"]) +
    0.25*(1 - hex_us_proj["n_temp_raw"])
)

hex_us_proj["sustain"] = (
    0.45*(hex_us_proj["n_renew_raw"]) +
    0.35*(hex_us_proj["n_stability_raw"]) +
    0.20*(1 - hex_us_proj["n_co2_raw"])
)

hex_us_proj["dc_score_raw"] = (
    0.6 * hex_us_proj["profit"] +
    0.4 * hex_us_proj["sustain"]
)

from sklearn.neighbors import NearestNeighbors

centers = np.vstack(hex_us_proj.geometry.centroid.apply(lambda p: (p.x,p.y)))
nbrs = NearestNeighbors(n_neighbors=7).fit(centers)
d, idx = nbrs.kneighbors(centers)

smooth = np.array([hex_us_proj["dc_score_raw"].values[i].mean() for i in idx])
hex_us_proj["dc_score"] = smooth

hex_us = hex_us_proj.to_crs("EPSG:4326")

In [15]:
hex_us.explore(
    column="dc_score",
    cmap="BuGn",
    legend=True
)

In [16]:
# continental US bounding box
min_lat, max_lat = 24.5, 49.5
min_lon, max_lon = -124.7, -66.9

hex_conus = hex_us.cx[min_lon:max_lon, min_lat:max_lat]
hex_conus.explore(
    column="dc_score",
    cmap="BuGn",
    legend=True
)


- Reddis -> Cache
- Run a python file on aws lambda/ec2 

- User -> frontend -> python API (updates every 24 hours) (computation) -> calls database.